## Sloving Needle Master with Twin Delayed DDPG (TD3)
Code modified from https://github.com/nikhilbarhate99/TD3-PyTorch-BipedalWalker-v2 <br>


In [1]:
import numpy as np
import torch
import argparse
import os
import sys
import random
from environment import Environment
import utils
import TD3
import math
import matplotlib.pyplot as plt

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [12]:
class Args:
    policy_name = "TD3"
    env_name = "Needle Master"
    seed = 1e6
    start_timesteps = 5e3  # How many time steps purely random policy is run for
    eval_freq = 1e3 # How often (time steps) we evaluate
    max_timesteps = 1e6   # Max time steps to run environment for
    save_models = "store"
    expl_noise = 1    # Std of Gaussian exploration noise
    batch_size = 1000
    discount = 0.99   # Discount factor
    tau = 0.005         # Target network update rate
    policy_noise = 0.2   # Noise added to target policy during critic update
    noise_clip = 0.5
    policy_freq = 2  # Frequency of delayed policy updates
    max_size = 5e3
    random_freq = 2e3 
    random_interval = 5e2
    filename = 'environment_14.txt'
    
args=Args()

In [13]:
# Setup
random.seed(args.seed)
torch.manual_seed(random.randint(1, 10000))
if torch.cuda.is_available():
    args.device = torch.device('cuda')
    torch.cuda.manual_seed(random.randint(1, 10000))
    torch.backends.cudnn.enabled = False  # Disable nondeterministic ops (not sure if critical but better safe than sorry)
else:
    args.device = torch.device('cpu')

In [14]:
sys.path.insert(0, '/home/lifan/workspace/RL/needle_master_tools/data')

### Model evaluation

In [15]:
def evaluate_policy(policy, log_f, eval_episodes= 1):
    avg_reward = 0.
    eval_path = './evaluate/'
    if not os.path.exists(eval_path):
        os.mkdir(eval_path)
    for _ in range(eval_episodes):
        state = env.reset(log_f)
        done = False
        while not done:
            action = policy.select_action(state)
            # print("state: " + str(state))
            # print("action: " + str(action))
            next_state, reward, done = env.step(action, log_f)
            # print("next state: " + str(next_state))
            # print("done: " +str(done))
            state = next_state
            avg_reward += reward
        env.render(save_image=True, save_path=eval_path)

    avg_reward /= eval_episodes
    env.episode_reward = avg_reward

    print ("---------------------------------------")
    print ("Episode_num: %d, Evaluation over %d episodes: %f" % (env.episode_num, eval_episodes, avg_reward))
    print ("---------------------------------------")
    return avg_reward



In [ ]:
file_name = "%s_%s_%s_%s" % (args.policy_name, args.env_name, str(args.seed),1)
print ("---------------------------------------")
print ("Settings: %s" % (file_name))
print ("---------------------------------------")

if not os.path.exists("./results"):
    os.makedirs("./results")
if not os.path.exists("./pytorch_models"):
    os.makedirs("./pytorch_models")

## environment set up


""" Adding the log file """
logfile = "%s_%s" % (args.policy_name, args.env_name)
log_f = open("log_"+logfile+".txt","w+")
env = Environment(log_f, filename=args.filename)

# env.GetTargetPoint()
state_dim = 10
action_dim = 2
""""  for PID controller """
action_constrain = [10, np.pi/20]
parameter = [0.1,0.0009]

""" [lower bound],[higher bound] """
env.action_bound = np.array(([-1, -1],[1, 1]))  ## modified lower bound
max_action = 1.0

### for plotting
Reward = []
save_path = './out/'
""" start straightly """
evaluations = []

# Initialize policy
policy = TD3.TD3(state_dim, action_dim, max_action)
replay_buffer = utils.ReplayBuffer(args.max_size)

# Evaluate untrained policy
# evaluations = [evaluate_policy(policy)]


env.total_timesteps = 0
env.random_fre = 1000
timesteps_since_eval = 0
done = True

while env.total_timesteps < args.max_timesteps:

    # Evaluate episode
    if timesteps_since_eval >= args.eval_freq:
        timesteps_since_eval %= args.eval_freq
        evaluations.append(evaluate_policy(policy, log_f))

        policy.save(file_name, directory="./pytorch_models")
        np.save("./results/%s" % (file_name), evaluations)

        continue


    ## finish one episode, and train episode_times
    if done:
        log_f.write('~~~~~~~~~~~~~~~~~~~~~~~~ iteration {} ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~\n'.format(env.episode_num))


        ## load model
        # policy.load(file_name,"./pytorch_models")

        ## training as usual
            # if env.total_timesteps != 0 and env.episode_reward > 500:
        if env.total_timesteps != 0:
            print (("Total T: %d Episode Num: %d Episode T: %d Reward: %f") % (
                env.total_timesteps, env.episode_num, episode_timesteps, env.episode_reward))
            if env.episode_num % 1 == 0:
                env.render( save_image=True, save_path=save_path)

        if env.total_timesteps != 0:
            policy.train(replay_buffer, episode_timesteps, args.batch_size, args.discount, args.tau, args.policy_noise, args.noise_clip, args.policy_freq)


        Reward.append(env.episode_reward)

        # Reset environment
        state = env.reset(log_f)

        done = False

        env.episode_num += 1
        env.episode_reward = 0
        episode_timesteps = 0

        # """ exploration rate decay """
        # if env.total_timesteps % 1000 == 0 and args.expl_noise > 0:
        #     args.expl_noise -= 0.05

    # Select action randomly or according to policy
    if env.total_timesteps % args.random_freq < args.random_interval:
        action = env.sample_action()
#         print("randomly selected: " + str(action))
        # action = env.PIDcontroller(action_constrain, parameter, env.t)
        # print("PID controller: " +str(action))
    else:
        # print("state: " +str(state))
        action = policy.select_action(state)
        print("action based on polilcy:" + str(action))
        # print("action selected: " +str(action))
        if args.expl_noise != 0:
            action = (action + np.random.normal(0, args.expl_noise, size=2)).clip(
                env.action_bound[0,:], env.action_bound[1,:])


    ### select action only based on pure RL
    # action = policy.select_action(state)
    # print("action selected: " +str(action))


    # Perform action
    new_state, reward, done = env.step(action, log_f)

    done_bool = 0 if episode_timesteps + 1 == env.max_time else float(done)
    env.episode_reward += reward

    # Store data in replay buffer
    replay_buffer.add((state, new_state, action, reward, done_bool))
    # print("state: " + str(state))
    state = new_state

    episode_timesteps += 1
    env.total_timesteps += 1
    timesteps_since_eval += 1

plt.plot(range(len(Reward)), np.array(Reward), 'b')
plt.savefig('./results/episode reward.png')

plt.plot(range(len(policy.actor_loss)), policy.actor_loss, 'b')
plt.savefig('./results/actor loss.png')

plt.plot(range(len(policy.critic_loss)), policy.critic_loss, 'b')
plt.savefig('./results/critic loss.png')

plt.plot(range(len(evaluations)), np.array(evaluations), 'b')
plt.savefig('./results/evaluation reward.png')
print(evaluations)



---------------------------------------
Settings: TD3_Needle Master_1000000.0_1
---------------------------------------
Total T: 21 Episode Num: 1 Episode T: 21 Reward: -3263.097738
Total T: 32 Episode Num: 2 Episode T: 11 Reward: -1212.585337
Total T: 81 Episode Num: 3 Episode T: 49 Reward: -7205.027849
Total T: 125 Episode Num: 4 Episode T: 44 Reward: -7161.007733
Total T: 143 Episode Num: 5 Episode T: 18 Reward: -2370.589150
Total T: 193 Episode Num: 6 Episode T: 50 Reward: -5630.131528
Total T: 241 Episode Num: 7 Episode T: 48 Reward: -5555.100389
Total T: 250 Episode Num: 8 Episode T: 9 Reward: -1114.372978
Total T: 297 Episode Num: 9 Episode T: 47 Reward: -7064.102805
Total T: 349 Episode Num: 10 Episode T: 52 Reward: -7012.707205
Total T: 396 Episode Num: 11 Episode T: 47 Reward: -7524.107058
Total T: 446 Episode Num: 12 Episode T: 50 Reward: -7353.510149
Total T: 466 Episode Num: 13 Episode T: 20 Reward: -2746.967836
action based on polilcy:[-1. -1.]
action based on polilcy:[-1

action based on polilcy:[-1.         -0.99130017]
action based on polilcy:[-1.        -0.9983134]
action based on polilcy:[-1.        -0.9987683]
action based on polilcy:[-1.       -0.999966]
action based on polilcy:[-1.       -0.999321]
action based on polilcy:[-1.        -0.9564431]
action based on polilcy:[-1.        -0.9995839]
action based on polilcy:[-1.         -0.29496258]
action based on polilcy:[-1.         -0.55473757]
action based on polilcy:[-1.         -0.46476156]
action based on polilcy:[-1.        -0.9999744]
action based on polilcy:[-1.         0.0071043]
action based on polilcy:[-1.         -0.47137418]
action based on polilcy:[-1.        -0.9999991]
action based on polilcy:[-1. -1.]
action based on polilcy:[-1.        -0.9999999]
action based on polilcy:[-1.         -0.77180505]
action based on polilcy:[-1.        -0.9939459]
action based on polilcy:[-1.       -0.994128]
action based on polilcy:[-1.        -0.9943073]
action based on polilcy:[-1.         -0.99108565

action based on polilcy:[-1.        -0.9772363]
action based on polilcy:[-1.       -0.731555]
action based on polilcy:[-1.        -0.9276709]
action based on polilcy:[-1.         -0.65520394]
action based on polilcy:[-1.        -0.6090406]
action based on polilcy:[-1.        -0.5619935]
action based on polilcy:[-1.         -0.57899415]
action based on polilcy:[-1.        -0.6020205]
action based on polilcy:[-1.       -0.672865]
action based on polilcy:[-1.         -0.75162995]
action based on polilcy:[-1.         -0.92075956]
action based on polilcy:[-1.         -0.87207884]
action based on polilcy:[-1.        -0.4282342]
action based on polilcy:[-1.         -0.83958554]
action based on polilcy:[-1.         -0.13212968]
action based on polilcy:[-1.         -0.12437291]
action based on polilcy:[-1.         -0.03803368]
action based on polilcy:[-1.0000000e+00  7.1890827e-04]
action based on polilcy:[-1.          0.06363791]
action based on polilcy:[-1.          0.01326869]
action based o

action based on polilcy:[-1.     -0.9867]
action based on polilcy:[-1.         -0.75341123]
action based on polilcy:[-1.         -0.71386504]
action based on polilcy:[-1.         -0.75998056]
action based on polilcy:[-1.        -0.9738412]
action based on polilcy:[-1.        -0.8628572]
action based on polilcy:[-1.         -0.92506045]
action based on polilcy:[-1.        -0.6172056]
action based on polilcy:[-1.         -0.45205417]
action based on polilcy:[-0.99999994 -0.57645   ]
action based on polilcy:[-1.         -0.42987975]
action based on polilcy:[-1.       -0.376091]
action based on polilcy:[-1.         -0.23072918]
action based on polilcy:[-1.        -0.5731933]
action based on polilcy:[-1.         -0.19922839]
action based on polilcy:[-1.          0.01656745]
action based on polilcy:[-1.          0.03339807]
action based on polilcy:[-1.          0.16130213]
action based on polilcy:[-1.          0.05286923]
action based on polilcy:[-1.          0.10193295]
action based on poli

action based on polilcy:[-1.         -0.98444337]
action based on polilcy:[-1.         -0.62481356]
action based on polilcy:[-1.        -0.8801521]
action based on polilcy:[-1.        -0.6169386]
action based on polilcy:[-1.         -0.24326941]
action based on polilcy:[-1.         -0.21460535]
action based on polilcy:[-1.         -0.11848043]
action based on polilcy:[-1.         0.4337976]
action based on polilcy:[-1.          0.29659113]
action based on polilcy:[-1.          0.40119338]
action based on polilcy:[-1.          0.17964022]
action based on polilcy:[-1.          0.10929944]
action based on polilcy:[-1.          0.25770873]
action based on polilcy:[-1.          0.03158648]
action based on polilcy:[-1.         -0.10783487]
action based on polilcy:[-1.         -0.19531225]
action based on polilcy:[-1.       -0.478329]
action based on polilcy:[-1.         -0.36011857]
action based on polilcy:[-1.         -0.48062313]
action based on polilcy:[-1.         -0.24468352]
action bas

...

action based on polilcy:[0.13433531 0.8398242 ]
action based on polilcy:[-0.64121175 -0.98818016]
action based on polilcy:[-0.9487287  -0.87790877]
action based on polilcy:[-0.9433283  -0.87493217]
action based on polilcy:[-0.99709964 -0.7890347 ]
action based on polilcy:[-0.9998264  -0.74010724]
action based on polilcy:[-1.        -0.6615162]
action based on polilcy:[-1.        -0.5887164]
action based on polilcy:[-1.         -0.66357017]
action based on polilcy:[-1.        -0.6640984]
action based on polilcy:[-0.9999992  -0.68827844]
action based on polilcy:[-0.9748248  0.9999022]
action based on polilcy:[0.08295809 1.        ]
action based on polilcy:[-0.40941972  0.9973897 ]
action based on polilcy:[0.30593666 1.        ]
action based on polilcy:[-0.19176641  0.9991466 ]
action based on polilcy:[0.37168363 1.        ]
action based on polilcy:[0.3021925 1.       ]
action based on polilcy:[-0.11240507  1.        ]
action based on polilcy:[-0.7110189  1.       ]
action based on polilc

action based on polilcy:[0.02563891 0.87631917]
action based on polilcy:[-0.80871284 -0.9764943 ]
action based on polilcy:[-0.95534   -0.9029653]
action based on polilcy:[-0.9631258 -0.887904 ]
action based on polilcy:[-0.9999999  -0.96398664]
action based on polilcy:[-0.99986917 -0.7427356 ]
action based on polilcy:[-1.        -0.6539233]
action based on polilcy:[-0.99999994 -0.7245325 ]
action based on polilcy:[-1.         -0.65123475]
action based on polilcy:[-1.        -0.6029327]
action based on polilcy:[-1.         -0.48459503]
action based on polilcy:[-0.2784093   0.99999994]
action based on polilcy:[-0.9999967   0.99999434]
action based on polilcy:[-0.85031915  0.9993128 ]
action based on polilcy:[-0.99997187  0.83368826]
action based on polilcy:[-0.99962276  0.58478975]
action based on polilcy:[0.48894215 1.        ]
action based on polilcy:[-0.7866127   0.82449836]
action based on polilcy:[0.43736833 1.        ]
action based on polilcy:[0.05972039 0.99999994]
action based on 

action based on polilcy:[-0.02257921  0.8802572 ]
action based on polilcy:[-0.33008444 -0.9795435 ]
action based on polilcy:[-0.7561331 -0.9908129]
action based on polilcy:[-0.9932053  -0.80091804]
action based on polilcy:[-1.        -0.9156561]
action based on polilcy:[-1.         -0.75577855]
action based on polilcy:[-1.        -0.8012285]
action based on polilcy:[-1.        -0.6896523]
action based on polilcy:[-0.35716763  1.        ]
action based on polilcy:[-1.          0.99999756]
action based on polilcy:[-0.99999297  0.99993694]
action based on polilcy:[-0.24420989  1.        ]
action based on polilcy:[-0.4145827  1.       ]
action based on polilcy:[-0.970149  0.446828]
action based on polilcy:[-0.86702365  0.994872  ]
action based on polilcy:[0.5748735 1.       ]
action based on polilcy:[-0.75346076  0.8214208 ]
action based on polilcy:[-0.4937705  0.9999767]
action based on polilcy:[0.9406636 1.       ]
action based on polilcy:[0.4776642 1.       ]
action based on polilcy:[0.7

action based on polilcy:[-0.02862045  0.85949254]
action based on polilcy:[ 0.36398464 -0.99953455]
action based on polilcy:[-0.99108   -0.9073923]
action based on polilcy:[-0.9962274 -0.9985811]
action based on polilcy:[-0.99965084 -0.77084005]
action based on polilcy:[-0.9996505 -0.8383777]
action based on polilcy:[-0.9998812  -0.75190735]
action based on polilcy:[-1.         -0.65619063]
action based on polilcy:[-0.89902467  0.9999856 ]
action based on polilcy:[-0.3883548   0.99999994]
action based on polilcy:[-0.4435542  1.       ]
action based on polilcy:[-0.9984786  0.8562197]
action based on polilcy:[-0.45458704  0.99999785]
action based on polilcy:[-0.255419  1.      ]
action based on polilcy:[-0.9715591   0.99458957]
action based on polilcy:[-0.91184145  0.40851027]
action based on polilcy:[0.39925423 1.        ]
action based on polilcy:[-0.99974644  0.4511209 ]
action based on polilcy:[0.57184815 1.        ]
action based on polilcy:[-0.21500364  0.99709374]
action based on po

action based on polilcy:[-0.04101406  0.57892734]
action based on polilcy:[-0.07635925 -0.9487692 ]
action based on polilcy:[ 0.17079857 -0.9999997 ]
action based on polilcy:[-0.69674146 -0.9953674 ]
action based on polilcy:[-0.98884374 -0.83571297]
action based on polilcy:[-0.999987   -0.98181593]
action based on polilcy:[-0.999788  -0.7268226]
action based on polilcy:[0.0248542  0.99999934]
action based on polilcy:[-0.13195719  0.54593265]
action based on polilcy:[-0.1980035  0.8567341]
action based on polilcy:[0.1758598  0.37870443]
action based on polilcy:[0.15451558 0.25504723]
action based on polilcy:[0.29059732 0.4355584 ]
action based on polilcy:[-0.9674373   0.53628796]
action based on polilcy:[0.1797924  0.20132399]
action based on polilcy:[-0.306529    0.49657208]
action based on polilcy:[0.6552793 1.       ]
action based on polilcy:[0.9504046 1.       ]
action based on polilcy:[0.99773914 1.        ]
action based on polilcy:[0.97986823 1.        ]
action based on polilcy:[0